# Etude sur le paradoxe de Simpson

Paradoxe de Simpson, c'est quoi ca encore ? 

Un paradoxe plutot intéressant qui se cache dans les jeux de données. Il est important de le connaitre pour éviter des erruers monumentales surtout si on travaille en médecine pour analyser correctement des données de santé. 

Il se produit dans au moins deux cas:  
1) Un facteur de confusion qui ne saute pas aux yeux de prime abord mais qui se cache et qui va avoir un impact sur le résultat  final. 
2) les données ne sont pas réparties de manière homogène = ne suivent pas une distribution normalion (loi normale).

Utile pour aiguiser son esprit critique quant à ce qui nous est présenté dans la litterature, à la tv pour ne pas se méprendre. Une facon simple de s'en débarasser est de vérifier si notre jeu de données suit bien une distibution selon la loi normale. 

Pour le comprendre nous allons utiliser un jeu de données historique comparant le taux de mortalité de femmes fumeuses ou non sur 20 ans d'étude -> Appleton, David R., Joyce M. French, and Mark PJ Vanderpump. « Ignoring a covariate: An example of Simpson’s paradox. » The American Statistician 50.4 (1996): 340-341.

Avant de commencer importons les modules nécessaires à notre analyse: 

In [12]:
%matplotlib inline
import matplotlib.pyplot as plt
import pandas as pd


Chargeons les données depuis le lien donné par notre navigateur:

In [13]:
data_url = "https://gitlab.inria.fr/learninglab/mooc-rr/mooc-rr-ressources/-/raw/master/module3/Practical_session/Subject6_smoking.csv?inline=false"

Transformons ce jeu de données en DataFrame pandas pour pouvoir l'analyser comme il se doit. 

In [14]:
raw_data = pd.read_csv(data_url)

In [15]:
raw_data

Smoker Status   Age
0       Yes  Alive  21.0
1       Yes  Alive  19.3
2        No   Dead  57.5
3        No  Alive  47.1
4       Yes  Alive  81.4
5        No  Alive  36.8
6        No  Alive  23.8
7       Yes   Dead  57.5
8       Yes  Alive  24.8
9       Yes  Alive  49.5
10      Yes  Alive  30.0
11       No   Dead  66.0
12      Yes  Alive  49.2
13       No  Alive  58.4
14       No   Dead  60.6
15       No  Alive  25.1
16       No  Alive  43.5
17       No  Alive  27.1
18       No  Alive  58.3
19      Yes  Alive  65.7
20       No   Dead  73.2
21      Yes  Alive  38.3
22       No  Alive  33.4
23      Yes   Dead  62.3
24       No  Alive  18.0
25       No  Alive  56.2
26      Yes  Alive  59.2
27       No  Alive  25.8
28       No   Dead  36.9
29       No  Alive  20.2
...     ...    ...   ...
1284    Yes   Dead  36.0
1285    Yes  Alive  48.3
1286     No  Alive  63.1
1287     No  Alive  60.8
1288    Yes   Dead  39.3
1289     No  Alive  36.7
1290     No  Alive  63.8
1291     No   Dead  71.3
1292     No  Alive  57.7
1293     No  Alive  63.2
1294     No  Alive  46.6
1295    Yes   Dead  82.4
1296    Yes  Alive  38.3
1297    Yes  Alive  32.7
1298     No  Alive  39.7
1299    Yes   Dead  60.0
1300     No   Dead  71.0
1301     No  Alive  20.5
1302     No  Alive  44.4
1303    Yes  Alive  31.2
1304    Yes  Alive  47.8
1305    Yes  Alive  60.9
1306     No   Dead  61.4
1307    Yes  Alive  43.0
1308     No  Alive  42.1
1309    Yes  Alive  35.9
1310     No  Alive  22.3
1311    Yes   Dead  62.1
1312     No   Dead  88.6
1313     No  Alive  39.1

[1314 rows x 3 columns]

Nous avons donc dans cette étude 1314 femmes dont nous savons leur age et statut tabagique lors de la première étude ainsi que leur survie 20 ans plus tard. 
=> Etudions donc le taux de mortalité chez ces femmes fumeuses et non fumeuses en dividant le nombre de femmes décédées par le nombre de femmes totales dans chacune des catégories. 

Pour cela créons 2 catégories de femmes: les fumeuses (smokers) et les non fumeuses (non_smokers)

In [16]:
smokers = raw_data[raw_data['Smoker'] == 'Yes']
non_smokers = raw_data[raw_data['Smoker'] == 'No']

Il nous faudrait maintenant, dans ces 2 catégories de femmes, des sous groupes dans lesquels nous pourrions distinguer si la personne est en vie ou nous après 20 ans.

In [21]:
Alive_smokers = smokers[smokers['Status'] == 'Alive']
Dead_smokers = smokers[smokers['Status'] == 'Dead']
Alive_non_smokers = non_smokers[non_smokers['Status'] == 'Alive']
Dead_non_smokers = non_smokers[non_smokers['Status'] == 'Dead']



len(smokers) + len(non_smokers)

In [22]:
len(Dead_non_smokers), len(Alive_non_smokers)

(230, 502)

In [23]:
len(Dead_smokers), len(Alive_smokers)

(139, 443)

Dans le but de présenter les données sous forme d'un tableau, il nous faut créer une liste de liste, autrement un dictionnaire. 

Représentez dans un tableau le nombre total de femmes vivantes et décédées sur la période en fonction de leur habitude de tabagisme. Calculez dans chaque groupe (fumeuses / non fumeuses) le taux de mortalité (le rapport entre le nombre de femmes décédées dans un groupe et le nombre total de femmes dans ce groupe). Vous pourrez proposer une représentation graphique de ces données et calculer des intervalles de confiance si vous le souhaitez. En quoi ce résultat est-il surprenant ?

Reprenez la question 1 (effectifs et taux de mortalité) en rajoutant une nouvelle catégorie liée à la classe d'âge. On considérera par exemple les classes suivantes : 18-34 ans, 34-54 ans, 55-64 ans, plus de 65 ans. En quoi ce résultat est-il surprenant ? Arrivez-vous à expliquer ce paradoxe ? De même, vous pourrez proposer une représentation graphique de ces données pour étayer vos explications.

Afin d'éviter un biais induit par des regroupements en tranches d'âges arbitraires et non régulières, il est envisageable d'essayer de réaliser une régression logistique. Si on introduit une variable Death valant 1 ou 0 pour indiquer si l'individu est décédé durant la période de 20 ans, on peut étudier le modèle Death ~ Age pour étudier la probabilité de décès en fonction de l'âge selon que l'on considère le groupe des fumeuses ou des non fumeuses. Ces régressions vous permettent-elles de conclure sur la nocivité du tabagisme ? Vous pourrez proposer une représentation graphique de ces régressions (en n'omettant pas les régions de confiance).

Déposez votre étude dans FUN

In [20]:
Mortality_rate_smokers = Dead_smokers.value_counts // smokers.value_counts()

AttributeError: 'DataFrame' object has no attribute 'value_counts'